In [1]:
import os
if "models" not in os.listdir("."):
    os.chdir("../..")

In [2]:
%load_ext autoreload
%autoreload 2
import penzai
import jax_smi
jax_smi.initialise_tracking()
from penzai import pz
pz.ts.register_as_default()
pz.ts.register_autovisualize_magic()
pz.enable_interactive_context()

In [3]:
from micrlhf.llama import LlamaTransformer
llama = LlamaTransformer.from_pretrained("models/gemma-2b-it.gguf", from_type="gemma", load_eager=True, device_map="tpu:0")

In [4]:
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("alpindale/gemma-2b")
tokenizer.padding_side = "right"

In [5]:
from sprint.task_vector_utils import load_tasks, ICLRunner
tasks = load_tasks()

In [6]:
def check_if_single_token(token):
    return len(tokenizer.tokenize(token)) == 1

task_name = "es_en"

task = tasks[task_name]

print(len(task))

task = {
    k:v for k,v in task.items() if check_if_single_token(k) and check_if_single_token(v)
}

print(len(task))

pairs = list(task.items())

763
346


In [26]:
from sprint.task_vector_utils import logprob_loss
from functools import partial

sep = 3978
pad = 0

def metric_fn(logits, resids, tokens):
    return logprob_loss(logits, tokens, sep=sep, pad_token=pad, n_first=2)

In [62]:
from micrlhf.llama import LlamaBlock, LlamaAttention
from micrlhf.utils.activation_manipulation import ActivationAddition, wrap_vector
from functools import partial
import jax.numpy as jnp
from penzai import pz
import jax

@partial(jax.jit, static_argnames=("metric", "batched"))
def run_with_add(additions_pre, additions_mid, tokens, metric, batched=False, llama=None):
    get_resids = llama.select().at_instances_of(LlamaBlock).apply_with_selected_index(lambda i, x:
        pz.nn.Sequential([
            pz.de.TellIntermediate.from_config(tag=f"resid_pre_{i}"),
            x
        ])
    )
    get_resids = get_resids.select().at_instances_of(LlamaBlock).apply_with_selected_index(lambda l, b: b.select().at_instances_of(pz.nn.Residual).apply_with_selected_index(lambda i, x: x if i == 0 else pz.nn.Sequential([
        pz.de.TellIntermediate.from_config(tag=f"resid_mid_{l}"),
        x,
    ])))


    get_resids = get_resids.select().at_instances_of(LlamaAttention).apply_with_selected_index(lambda i, x: x.select().at_instances_of(pz.nn.Softmax).apply(lambda b: pz.nn.Sequential([
        b,
        pz.de.TellIntermediate.from_config(tag=f"attn_{i}"),
    ])))

    get_resids = pz.de.CollectingSideOutputs.handling(get_resids, tag_predicate=lambda x: True)
    make_additions = get_resids.select().at_instances_of(LlamaBlock).apply_with_selected_index(lambda i, x:
        pz.nn.Sequential([
            ActivationAddition(pz.nx.wrap(additions_pre[i], *(("batch",) if batched else ()), "seq", "embedding"), "all"),
            x
        ])
    )
    make_additions = make_additions.select().at_instances_of(LlamaBlock).apply_with_selected_index(lambda l, b: b.select().at_instances_of(pz.nn.Residual).apply_with_selected_index(lambda i, x: x if i == 0 else pz.nn.Sequential([
        ActivationAddition(pz.nx.wrap(additions_mid[l], *(("batch",) if batched else ()), "seq", "embedding"), "all"),
        x,
    ])))
    tokens_wrapped = pz.nx.wrap(tokens, "batch", "seq")
    logits, resids = make_additions(llama.inputs.from_basic_segments(tokens_wrapped))
    return metric(logits.unwrap("batch", "seq", "vocabulary"), resids, tokens), (logits, resids[::3], resids[1::3], resids[2::3])


@partial(jax.jit, static_argnames=("metric",))
def get_metric_resid_grad(tokens, llama=llama, metric=metric_fn):
    additions = [jnp.zeros(tokens.shape + (llama.config.hidden_size,)) for _ in range(llama.config.num_layers)]
    batched = tokens.ndim > 1
    (metric, (logits, resids_pre, qk, resids_mid)), (grad_pre, grad_mid) = jax.value_and_grad(run_with_add, argnums=(0, 1), has_aux=True)(additions, additions, tokens, metric, batched=batched, llama=llama)
    return (
        metric,
        [r.value.unwrap("batch", "seq", "embedding") for r in resids_pre],
        [r.value.unwrap("batch", "seq", "embedding") for r in resids_mid],
        [r.value.unwrap("batch", "kv_heads", "q_rep", "seq", "kv_seq") for r in qk],
        grad_pre,
        grad_mid
    )


In [45]:
batch_size = 8 
n_shot=20
max_seq_len = 128
seed = 10

In [46]:
runner = ICLRunner(task_name, pairs, batch_size=batch_size, n_shot=n_shot, max_seq_len=max_seq_len, seed=seed)

In [47]:
from sprint.task_vector_utils import tokenized_to_inputs

train_tokens = runner.get_tokens(
    runner.train_pairs, tokenizer
)["input_ids"]

In [48]:
# train_tokens = jnp.asarray(train_tokens)
# train_tokens = jax.device_put(train_tokens, jax.sharding.NamedSharding(llama.mesh, jax.sharding.PartitionSpec("dp", "sp")))
# train_tokens = pz.nx.wrap(train_tokens, "batch", "seq").untag("batch").tag("batch")


In [63]:
metric_value, resids_pre, resids_mid, qk, grad_pre, grad_mid = get_metric_resid_grad(train_tokens, llama=llama)

{'seq': 128, 'batch': 8, 'kv_heads': 1, 'q_rep': 8, 'kv_seq': 128}


In [69]:
from micrlhf.utils.load_sae import get_nev_it_sae_suite

In [16]:
layer = 12

In [17]:
sae = get_nev_it_sae_suite(layer=layer)

--2024-07-11 19:16:51--  https://huggingface.co/nev/gemma-2b-saex-test/resolve/main/it-l12-residual-test-run-1-2.00E-05/sae_weights.safetensors?download=true
Resolving huggingface.co (huggingface.co)... 108.157.142.74, 108.157.142.55, 108.157.142.53, ...
Connecting to huggingface.co (huggingface.co)|108.157.142.74|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs-us-1.huggingface.co/repos/41/2a/412ab25f82137bafe7bc1655651e4e6f7eeae46d2504fc103b2b3624ff745ff8/482902b98aceb9c73042f4ebd95aa5742af2d793c8812407b806a3166900a2ef?response-content-disposition=attachment%3B+filename*%3DUTF-8%27%27sae_weights.safetensors%3B+filename%3D%22sae_weights.safetensors%22%3B&Expires=1720984611&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTcyMDk4NDYxMX19LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy11cy0xLmh1Z2dpbmdmYWNlLmNvL3JlcG9zLzQxLzJhLzQxMmFiMjVmODIxMzdiYWZlN2JjMTY1NTY1MWU0ZTZmN2VlYWU0NmQyNTA0ZmMxMDNiMmIzNjI0ZmY3NDVmZjgv

In [77]:
resid = results[1][layer]

In [78]:
resid = resid

In [79]:
resid

<jax.Array float32(8, 128, 2048) ≈0.0014 ±1.4 [≥-4.7e+02, ≤3e+02] nonzero:2_097_152>

In [65]:
# grad_mid[0]  # 8, 128, 2048

<jax.Array float32(8, 128, 2048) ≈1.9e-08 ±7.6e-05 [≥-0.0095, ≤0.012] zero:638_976 nonzero:1_458_176>

In [67]:
def weights_to_resid(weights):
    if "s_gate" in sae:
        weights = (weights > 0) * jax.nn.relu(weights * jax.nn.softplus(sae["s_gate"]) * sae.get("scaling_factor", 1.0) + sae["b_gate"])   
    else:
        weights = jax.nn.relu(weights)

    recon = jnp.einsum("fv,bsf->bsv", sae["W_dec"], weights)
    # recon = recon.astype('bfloat16')
    return recon

In [66]:
from micrlhf.utils.load_sae import sae_encode_gated



In [72]:
from tqdm.auto import tqdm

def sfc_simple(grad, resid, sae):
    pre_relu, post_relu, recon = sae_encode_gated(sae, resid)
    sae_grad, = jax.vjp(weights_to_resid, post_relu)[1](grad)
    indirect_effects = sae_grad * post_relu
    return indirect_effects
layers = [6,] + list(range(8, 17))
for layer in tqdm(layers):
    r_pre, r_mid, g_mid = resids_pre[layer], resids_mid[layer], grad_mid[layer]
    sae = get_nev_it_sae_suite(layer=layer, label="attn_out")
    indirect_effects = sfc_simple(g_mid, r_mid - r_pre, sae)
    display((indirect_effects > 0).sum(-1))

# for layer, (r_pre, g_pre) in enumerate(zip(resids_pre, grad_pre)):
for layer in tqdm(layers):
    r_pre, g_pre = resids_pre[layer], grad_pre[layer]
    sae = get_nev_it_sae_suite(layer=layer)
    indirect_effects = sfc_simple(g_pre, r_pre, sae)
    display((indirect_effects != 0).sum(-1))

[[1 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [1 0 0 ... 0 0 0]
 ...
 [1 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]


--2024-07-11 20:40:07--  https://huggingface.co/nev/gemma-2b-saex-test/resolve/main/it-l8-attn_out-test-run-1-2.00E-05/sae_weights.safetensors?download=true
Resolving huggingface.co (huggingface.co)... 108.157.142.50, 108.157.142.74, 108.157.142.53, ...
Connecting to huggingface.co (huggingface.co)|108.157.142.50|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs-us-1.huggingface.co/repos/41/2a/412ab25f82137bafe7bc1655651e4e6f7eeae46d2504fc103b2b3624ff745ff8/818e2aaa054ff1666e77883325a85a3494c975a70e2cc4bbcffed883ae08851e?response-content-disposition=attachment%3B+filename*%3DUTF-8%27%27sae_weights.safetensors%3B+filename%3D%22sae_weights.safetensors%22%3B&Expires=1720989607&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTcyMDk4OTYwN319LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy11cy0xLmh1Z2dpbmdmYWNlLmNvL3JlcG9zLzQxLzJhLzQxMmFiMjVmODIxMzdiYWZlN2JjMTY1NTY1MWU0ZTZmN2VlYWU0NmQyNTA0ZmMxMDNiMmIzNjI0ZmY3NDVmZjgvO

[[0 1 1 ... 0 0 0]
 [1 0 1 ... 0 0 0]
 [1 0 0 ... 0 0 0]
 ...
 [1 0 0 ... 0 0 0]
 [1 1 0 ... 0 0 0]
 [1 0 0 ... 0 0 0]]


--2024-07-11 20:40:34--  https://huggingface.co/nev/gemma-2b-saex-test/resolve/main/it-l9-attn_out-test-run-1-2.00E-05/sae_weights.safetensors?download=true
Resolving huggingface.co (huggingface.co)... 108.157.142.50, 108.157.142.55, 108.157.142.74, ...
Connecting to huggingface.co (huggingface.co)|108.157.142.50|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs-us-1.huggingface.co/repos/41/2a/412ab25f82137bafe7bc1655651e4e6f7eeae46d2504fc103b2b3624ff745ff8/4deb1770aadfd566e0e6af58ee77509609d4727efff621cc6a58a632fd9d3faa?response-content-disposition=attachment%3B+filename*%3DUTF-8%27%27sae_weights.safetensors%3B+filename%3D%22sae_weights.safetensors%22%3B&Expires=1720989635&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTcyMDk4OTYzNX19LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy11cy0xLmh1Z2dpbmdmYWNlLmNvL3JlcG9zLzQxLzJhLzQxMmFiMjVmODIxMzdiYWZlN2JjMTY1NTY1MWU0ZTZmN2VlYWU0NmQyNTA0ZmMxMDNiMmIzNjI0ZmY3NDVmZjgvN

[[0 3 0 ... 0 0 0]
 [4 1 2 ... 0 0 0]
 [5 5 5 ... 0 0 0]
 ...
 [4 3 5 ... 0 0 0]
 [4 2 3 ... 0 0 0]
 [4 3 3 ... 0 0 0]]


...

--2024-07-11 20:42:48--  https://huggingface.co/nev/gemma-2b-saex-test/resolve/main/it-l14-attn_out-test-run-1-2.00E-05/sae_weights.safetensors?download=true
Resolving huggingface.co (huggingface.co)... 108.156.211.51, 108.156.211.125, 108.156.211.95, ...
Connecting to huggingface.co (huggingface.co)|108.156.211.51|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs-us-1.huggingface.co/repos/41/2a/412ab25f82137bafe7bc1655651e4e6f7eeae46d2504fc103b2b3624ff745ff8/71d5a89d5d7288b6887aa7d7a6f1ff8ed9d7cb3b57be4b33b34b170156da05b6?response-content-disposition=attachment%3B+filename*%3DUTF-8%27%27sae_weights.safetensors%3B+filename%3D%22sae_weights.safetensors%22%3B&Expires=1720989768&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTcyMDk4OTc2OH19LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy11cy0xLmh1Z2dpbmdmYWNlLmNvL3JlcG9zLzQxLzJhLzQxMmFiMjVmODIxMzdiYWZlN2JjMTY1NTY1MWU0ZTZmN2VlYWU0NmQyNTA0ZmMxMDNiMmIzNjI0ZmY3NDVmZjg

[[4 3 1 ... 0 0 0]
 [1 3 3 ... 0 0 0]
 [6 2 1 ... 0 0 0]
 ...
 [3 5 4 ... 0 0 0]
 [5 3 3 ... 0 0 0]
 [4 1 1 ... 0 0 0]]


...... .......... 93% 88.1M 1s
491800K .......... .......... .......... .......... .......... 93% 79.3M 1s
491850K .......... .......... .......... .......... .......... 93% 92.1M 1s
491900K .......... .......... .......... .......... .......... 93%  248M 1s
491950K .......... .......... .......... .......... .......... 93% 80.9M 1s
492000K .......... .......... .......... .......... .......... 93% 92.0M 1s
492050K .......... .......... .......... .......... .......... 93% 19.4M 1s
492100K .......... .......... .......... .......... .......... 93% 9.49M 1s
492150K .......... .......... .......... .......... .......... 93%  105M 1s
492200K .......... .......... .......... .......... .......... 93% 30.3M 1s
492250K .......... .......... .......... .......... .......... 93%  408M 1s
492300K .......... .......... .......... .......... .......... 93%  130M 1s
492350K .......... .......... .......... .......... .......... 93%  299M 1s
492400K .......... .......... .......... .......... .....

[[14  6 12 ...  0  0  0]
 [15  8 10 ...  0  0  0]
 [24 12  6 ...  0  0  0]
 ...
 [21 12 13 ...  0  0  0]
 [23 15 14 ...  0  0  0]
 [25  6 11 ...  0  0  0]]


--2024-07-11 20:43:15--  https://huggingface.co/nev/gemma-2b-saex-test/resolve/main/it-l16-attn_out-test-run-1-2.00E-05/sae_weights.safetensors?download=true
Resolving huggingface.co (huggingface.co)... 108.156.211.125, 108.156.211.95, 108.156.211.90, ...
Connecting to huggingface.co (huggingface.co)|108.156.211.125|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs-us-1.huggingface.co/repos/41/2a/412ab25f82137bafe7bc1655651e4e6f7eeae46d2504fc103b2b3624ff745ff8/63d2d3e062ca3027f5bc1c2bd5c47d9552fe02f4a2273e285f5d02f18702bbfa?response-content-disposition=attachment%3B+filename*%3DUTF-8%27%27sae_weights.safetensors%3B+filename%3D%22sae_weights.safetensors%22%3B&Expires=1720989795&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTcyMDk4OTc5NX19LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy11cy0xLmh1Z2dpbmdmYWNlLmNvL3JlcG9zLzQxLzJhLzQxMmFiMjVmODIxMzdiYWZlN2JjMTY1NTY1MWU0ZTZmN2VlYWU0NmQyNTA0ZmMxMDNiMmIzNjI0ZmY3NDVmZj

In [89]:
post_relu

<jax.Array float32(8, 128, 32768) ≈0.0014 ±0.39 [≥0.0, ≤8e+02] zero:33_518_636 nonzero:35_796>

In [90]:
sae_grad = jax.vjp(weights_to_resid, post_relu)[1](results[2][layer])

In [91]:
sae_grad

(<jax.Array float32(8, 128, 32768) ≈-5.4e-09 ±2.4e-05 [≥-0.037, ≤0.074] zero:33_526_736 nonzero:27_696>,)

In [69]:
sae_grad

(# jax.Array float32(32768,) ≈9.4e-11 ±1.7e-08 [≥-0.0, ≤3.1e-06] zero:32_767 nonzero:1
   Array([ 0.,  0.,  0., ..., -0., -0., -0.], dtype=float32)
 ,)

In [ ]:
post_relu.dtype

In [59]:
post_relu.shape     

(2048, 32768)

In [37]:
llama

LlamaTransformer(
  #╭┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄╮
  # Input: LlamaInputs(tokens=<tokens>, attention_mask=<attention mask>, positions=<positions>)
  # Output: <unnormalized logits>
  #╰┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄┄╯
  config=LlamaConfig(vocab_size=256000, hidden_size=2048, intermediate_size=16384, num_attention_heads=8, num_key_value_heads=1, head_dim=256, num_layers=18, parameter_dtype=jax.numpy.bfloat16, activation_dtype=jax.numpy.bfloat16, act_fn='gelu', resid_rescale=<jax.Array(45.25, dtype=float16)>),
  body=WithSideInputsFromInputTuple(handler_id='WithSideInputsFromInputTuple_2f504', body=Sequential(sublayers=[EmbeddingLookup(table=EmbeddingTable(embeddings=Parameter(value=<NamedArray bfloat16(| vocabulary:256000, embedding:2048) ≈0.0016 ±0.18 [≥-9.8, ≤6.0] zero:5_685_388 nonzero:518_602_612 (wrapping jax.Array)>, name='embed.embeddings'), vocabulary_axis='vocabulary')), ConstantRescale(by=<jax.Array(45.25, dtype=float16)>), WithConstantSideInputsNonPytree(handler_id='WithConstantSideInputsNonPytree_febf8', body=ConstrainedSharding(mesh=HandledSideInputRef(handler_id='WithConstantSideInputsNonPytree_febf8', tag='mesh'), axis_name_to_mesh_name=HandledSideInputRef(handler_id='WithConstantSideInputsNonPytree_febf8', tag='axis_name_to_mesh_name')), side_inputs={'axis_name_to_mesh_name': {'neurons': 'mp', 'kv_heads': 'mp', 'seq': 'sp', 'batch': 'dp', 'dp': 'dp', 'sp': 'sp', 'mp': 'mp'}, 'mesh': Mesh(device_ids=array([[[0]]]), axis_names=('dp', 'sp', 'mp'))}), Sequential(sublayers=[LlamaBlock(sublayers=[WithConstantSideInputsNonPytree(handler_id='WithConstantSideInputsNonPytree_febf8', body=ConstrainedSharding(mesh=HandledSideInputRef(handler_id='WithConstantSideInputsNonPytree_febf8', tag='mesh'), axis_name_to_mesh_name=HandledSideInputRef(handler_id='WithConstantSideInputsNonPytree_febf8', tag='axis_name_to_mesh_name')), side_inputs={'axis_name_to_mesh_name': {'neurons': 'mp', 'kv_heads': 'mp', 'seq': 'sp', 'batch': 'dp', 'dp': 'dp', 'sp': 'sp', 'mp': 'mp'}, 'mesh': Mesh(device_ids=array([[[0]]]), axis_names=('dp', 'sp', 'mp'))}), Residual(delta=Sequential(sublayers=[RMSLayerNorm(sublayers=[RMSStandardize(across=('embedding',), epsilon=<jax.Array(9.98378e-07, dtype=bfloat16)>), Linear(weights=Parameter(value=<NamedArray bfloat16(| embedding:2048) ≈2.6 ±1.4 [≥-0.27, ≤9.8] zero:9 nonzero:2_039 (wrapping jax.Array)>, name='blocks.0.pre_attn_norm.scale.weights'), in_axis_names=(), out_axis_names=())]), CastToDType(dtype=jax.numpy.bfloat16), LlamaAttention(input_to_query=Sequential(sublayers=[Linear(weights=Parameter(value=<NamedArray bfloat16(| embedding:2048, kv_heads:1, q_rep:8, projection:256) ≈2.2e-06 ±0.0086 [≥-0.21, ≤0.18] zero:68_150 nonzero:4_126_154 (wrapping jax.Array)>, name='blocks.0.attn.query.weights'), in_axis_names=('embedding',), out_axis_names=('kv_heads', 'q_rep', 'projection')), ApplyRoPE(embedding_axis='projection', max_wavelength=10000, positions=HandledSideInputRef(handler_id='WithSideInputsFromInputTuple_2f504', tag='positions')), ConstantRescale(by=<jax.Array(0.0625, dtype=bfloat16)>)]), input_to_key=Sequential(sublayers=[Linear(weights=Parameter(value=<NamedArray bfloat16(| embedding:2048, kv_heads:1, projection:256) ≈-5.5e-06 ±0.012 [≥-0.098, ≤0.1] zero:9_918 nonzero:514_370 (wrapping jax.Array)>, name='blocks.0.attn.key.weights'), in_axis_names=('embedding',), out_axis_names=('kv_heads', 'projection')), ApplyRoPE(embedding_axis='projection', max_wavelength=10000, positions=HandledSideInputRef(handler_id='WithSideInputsFromInputTuple_2f504', tag='positions')), CastToDType(dtype=jax.numpy.bfloat16)]), input_to_value=Sequential(sublayers=[Linear(weights=Parameter(value=<NamedArray bfloat16(| embedding:2048, kv_heads:1, projection:256) ≈5.4e-05 ±0.017 [≥-0.25, ≤0.23] zero:13_577 nonzero:510_711 (wrapping jax.Array)>, name='blocks.0.attn.value.weights'), in_axis_names=('embedding',), out_axis_names=('kv_heads', 'projection')), CastToDType(dtype=jax.numpy.bfloat16)]), query_key_to_at